In [1]:
import numpy as np
import chess
import chess.uci
import json
import time
import random
import sys
import IPython.core.debugger as db
import pickle

In [2]:
def getNormX(position):
    return (position%8.0)/7.0
def getNormY(position):
    return float(position/8)/7.0

In [3]:
def calcGlobalFeatures(board):
    #side2Move
    #THIS IS PASSED DIRECTLY TO SECOND LAYER
    side2Move = [float(board.turn)]
    
    #king positions (this is covered elsewhere, but in a different group)
    #THIS IS PASSED DIRECTLY TO SECOND LAYER
    kingPosition = [getNormX(board.king(chess.WHITE)), 
        getNormY(board.king(chess.WHITE)), 
        getNormX(board.king(chess.BLACK)),
        getNormY(board.king(chess.BLACK))]
    
    #castlingRights
    #THIS IS PASSED DIRECTLY TO SECOND LAYER (I think)
    castlingRights = [float(board.has_kingside_castling_rights(chess.WHITE)), 
        float(board.has_queenside_castling_rights(chess.WHITE)), 
        float(board.has_kingside_castling_rights(chess.BLACK)), 
        float(board.has_queenside_castling_rights(chess.BLACK))]
    
    #numOfEachPieceType 
    #THIS IS PASSED DIRECTLY TO SECOND LAYER
    numOfEachPieceType = [len(board.pieces(chess.PAWN, chess.WHITE))/8.0, 
        len(board.pieces(chess.KNIGHT, chess.WHITE))/2.0,
        len(board.pieces(chess.BISHOP, chess.WHITE))/2.0,
        len(board.pieces(chess.ROOK, chess.WHITE))/2.0,
        len(board.pieces(chess.QUEEN, chess.WHITE))/1.0,
        len(board.pieces(chess.PAWN, chess.BLACK))/8.0, 
        len(board.pieces(chess.KNIGHT, chess.BLACK))/2.0,
        len(board.pieces(chess.BISHOP, chess.BLACK))/2.0,
        len(board.pieces(chess.ROOK, chess.BLACK))/2.0,
        len(board.pieces(chess.QUEEN, chess.BLACK))/1.0]
    return np.array(side2Move+kingPosition+castlingRights+numOfEachPieceType, dtype='float32')

In [4]:
#see variable SEE::SEE_MAT for values (WK is white king i think)
#NormalizeCount(SEE::SEE_MAT[WK] + SEE::SEE_MAT[WK] / 2 - SEE::SEE_MAT[whitePt], SEE::SEE_MAT[WK] * 2)
'''
static const Score SEE_MAT[14] = {
    1500, // WK
    975, // WQ
    500, // WR
    325, // WN
    325, // WB
    100, // WP
}
'''

def getLowestValueAttackerScore(board, position, color):
    attackers = board.attackers(color, position)
    #determine the lowest value attacker
    if not bool(attackers): #no attackers
        value = 2250.0 #makes the score 0
    elif bool(attackers & board.pieces(chess.PAWN, color)):
        value = 100.0
    elif bool(attackers & board.pieces(chess.BISHOP, color)):
        value = 325.0
    elif bool(attackers & board.pieces(chess.KNIGHT, color)):
        value = 325.0
    elif bool(attackers & board.pieces(chess.ROOK, color)):
        value = 500.0
    elif bool(attackers & board.pieces(chess.QUEEN, color)):
        value = 975.0
    else: #Must be a king attacker
        value = 1500.0
    return (2250.0 - value)/3000.0

In [5]:
def calcSquareFeatures(board):
    feats = []
    for position in range(64):
        feats.append(getLowestValueAttackerScore(board, position, chess.WHITE))
        feats.append(getLowestValueAttackerScore(board, position, chess.BLACK))
    return np.array(feats, dtype='float32')

In [6]:
def getSinglePieceFeatures(board, position, exists=True):
    #return array of pieceExists, XYposition, and attackers and defenders
    if exists:
        whiteAttackerScore = getLowestValueAttackerScore(board, 
                                 position, chess.WHITE)
        blackAttackerScore = getLowestValueAttackerScore(board, 
                                 position, chess.BLACK)
        feats = [1.0, getNormX(position), getNormY(position), 
                    whiteAttackerScore, blackAttackerScore]
    else:
        feats = [0.0, 0.0, 0.0, 0.0, 0.0]
    return feats
        
def getPawnFeatures(board, color):
    pawns = board.pieces(chess.PAWN, color)
    #Assign each pawn to a slot based on X position
    slots = []
    unassignedSlots = []
    unassignedPieces = []
    for x in range(8):
        column = pawns & chess.BB_FILES[x]
        if len(column) == 1: #exactly one pawn in column
            position = column.pop()
            slots.append(getSinglePieceFeatures(board, position))
        elif len(column) == 0: #no pawns in column
            slots.append(None)
            unassignedSlots.append(x)
        else: #more than one pawn in column
            position = column.pop()
            slots.append(getSinglePieceFeatures(board, position))
            unassignedPieces.extend(list(column))
    #match unpaired slots to pawns 
    for x in unassignedSlots:
        #make sure there are still extra pawns
        if len(unassignedPieces) > 0:
            #find closest pawn position
            position = min(unassignedPieces, key=lambda pos : abs(x-pos%8))
            slots[x] = getSinglePieceFeatures(board, position)
            unassignedPieces.remove(position)
        else:
            slots[x] = getSinglePieceFeatures(None, None, exists=False)
       
    #any extra pawns after this don't have a slot and are ignored
    #combine slots into a single array and return it

    return [feature for slot in slots for feature in slot]

def getPairPieceFeatures(board, pieceType, color):
    #for rooks, bishops, and knights, there are only 2 slots
    pieces = board.pieces(pieceType, color)
    if len(pieces) == 0:
        feats = getSinglePieceFeatures(None, None, exists=False)*2
    elif len(pieces) == 1:
        position = pieces.pop()
        emptyFeatures = getSinglePieceFeatures(None, None, exists=False)
        existingFeatures = getSinglePieceFeatures(board, position)
        if position%8 <4:
            feats = existingFeatures + emptyFeatures
        else:
            feats = emptyFeatures + existingFeatures
    else:
        position1 = pieces.pop()
        position2 = pieces.pop()
        feats1 = getSinglePieceFeatures(board, position1)
        feats2 = getSinglePieceFeatures(board, position2)
        if position1%8 < position2%8:
            feats = feats1 + feats2
        else:
            feats = feats2 + feats1
    return feats
    
def getQueenFeatures(board, color):
    queens = board.pieces(chess.QUEEN, color)
    if len(queens) > 0:
        position = queens.pop()
        feats = getSinglePieceFeatures(board, position)
    else:
        feats = getSinglePieceFeatures(None, None, exists=False)
    return feats
    
def getKingFeatures(board, color): #maybe not needed
    kings = board.pieces(chess.KING, color)
    if len(kings) > 0:
        position = kings.pop()
        feats = getSinglePieceFeatures(board, position)
    else: #this should never happen
        feats = getSinglePieceFeatures(None, None, exists=False)
    return feats

#the main function for this cell:
def calcPieceFeatures(board):
    pairPieces = [chess.ROOK, chess.BISHOP, chess.KNIGHT]
    pairPiecesFeatures = []
    for pieceType in pairPieces:
        pairPiecesFeatures.extend(getPairPieceFeatures(board, pieceType, chess.WHITE))
        pairPiecesFeatures.extend(getPairPieceFeatures(board, pieceType, chess.BLACK))
    pieceFeatures = np.array(getPawnFeatures(board, chess.WHITE)
                     +getPawnFeatures(board, chess.BLACK)
                     +pairPiecesFeatures
                     +getQueenFeatures(board, chess.WHITE)
                     +getQueenFeatures(board, chess.BLACK)
                     +getKingFeatures(board, chess.WHITE)
                     +getKingFeatures(board, chess.BLACK), dtype='float32')
    
    return pieceFeatures

In [104]:
def checkRestartEngine(force=False):
    if('engine' not in globals()):
        global engine 
        engine = chess.uci.popen_engine("stockfish")
        engine.debug(True)
        global infoHandler
        infoHandler = chess.uci.InfoHandler()
        engine.info_handlers.append(infoHandler)
        global computeTime
        computeTime = 50
    if force or not engine.is_alive():
        engine = chess.uci.popen_engine("stockfish")
        engine.debug(True)
        infoHandler = chess.uci.InfoHandler()
        engine.info_handlers.append(infoHandler)

In [ ]:
def getBestMove(board):
    checkRestartEngine()
    engine.ucinewgame()
    engine.position(board)
    possibleMoves = list(board.pseudo_legal_moves)
    possibleMoves.append(chess.Move(0, 0))
    try:
        bestMove = engine.go(searchmoves=possibleMoves, movetime=computeTime)[0]
        if bestMove == None: bestMove = chess.Move(0,0)
    except chess.uci.EngineTerminatedException as e:
        print('Error processing board and best move:')
        print(board)
        print(move)
        print(infoHandler.info)
        print(e)
        print('')
        checkRestartEngine(force=True)
        bestMove = random.choice(possibleMoves)

In [ ]:
def calcLabel(board, move, bestMove):
    return np.array([bestMove == move], dtype='float32')

In [106]:
def calcMoveRankings(board):
    moves = list(board.pseudo_legal_moves)
    moves.append(chess.Move(0, 0))
    scores = {}
    for move in moves:
        checkRestartEngine()
        engine.ucinewgame()
        engine.position(board)
        try:
            engine.go(searchmoves=[move], movetime=computeTime)[0]
            scores[move] = infoHandler.info['score'][1].cp
        except chess.uci.EngineTerminatedException as e:
            print('Error processing board and move ranking:')
            print(board)
            print(move)
            print(infoHandler.info)
            print(e)
            print('')
            checkRestartEngine(force=True)
            scores[move] = 0
    moves.sort(key=lambda move: scores[move], reverse=True)
    rankings = {}
    for i, move in enumerate(moves):
            rankings[move] = i
    return rankings

In [107]:
def calcMoveFeatures(board, move):
    #from square
    fromPos = move.from_square
    fromX = getNormX(fromPos)
    fromY = getNormY(fromPos)
    #to square
    toPos = move.to_square
    toX = getNormX(toPos)
    toY = getNormY(toPos)
    #piece type
    pieceTypeLabel = board.piece_type_at(fromPos)
    pieceType = [0.0]*6
    if pieceTypeLabel != None:
        pieceType[pieceTypeLabel-1] = 1.0 
    #promotion type (if any)
    promotion = [0.0]*6
    if move.promotion != None:
        promotion[move.promotion-1] = 1.0
    return np.array([fromX, fromY, toX, toY]+pieceType
                    +promotion, 
                    dtype='float32')

In [ ]:
def fen2Features(fen):
    checkRestartEngine()
    board = chess.Board(fen)
    nullMove = chess.Move(0, 0) #null move
    bestMove = getBestMove(board)
    moveRankings = calcMoveRankings(board)
    #consider all possible moves (including no move)
    globalFeatures = calcGlobalFeatures(board)
    pieceFeatures = calcPieceFeatures(board)
    squareFeatures = calcSquareFeatures(board)
    moveFeatures = calcMoveFeatures(board, nullMove)
    moveRanking = np.array([moveRankings[nullMove]/20.0], dtype='float32')
    label = calcLabel(board, nullMove, bestMove)
    
    features = [{'globalFeatures': globalFeatures, 
                 'pieceFeatures':pieceFeatures, 
                 'squareFeatures':np.concatenate((squareFeatures,moveFeatures)),
                 'moveRankings':moveRanking,
                 'labels':label}]
    possibleMoves = list(board.pseudo_legal_moves)
    possibleMoves.append(nullMove)
    for move in possibleMoves:
        globalFeatures = calcGlobalFeatures(board)
        pieceFeatures = calcPieceFeatures(board)
        squareFeatures = calcSquareFeatures(board)
        moveFeatures = calcMoveFeatures(board, move)
        moveRanking = np.array([moveRankings[move]/20.0], dtype='float32')
        label = calcLabel(board, move, bestMove)
        features.append({'globalFeatures': globalFeatures, 
                         'pieceFeatures':pieceFeatures, 
                         'squareFeatures':np.concatenate((squareFeatures,moveFeatures)),
                         'moveRankings':moveRanking,
                         'labels':label})
    return features


In [109]:
def randomSearchSample(baseFens, depth=1):
    if depth < 1:
        return []
    if type(baseFens) != list:
        baseFens = [baseFens]
    sampledFenSet = []
    fenSet = []
    threshold = 0.95
    for baseFen in baseFens:
        board = chess.Board(baseFen)
        #consider all possible moves (including no move)
        fenSet.append(baseFen)
        if random.random() > threshold:
            sampledFenSet.append(baseFen)
        for move in board.pseudo_legal_moves:
            board.push(move)
            if board.king(chess.WHITE) == None or board.king(chess.BLACK) == None:
                #db.set_trace()
                board.pop()
                continue
            fenSet.append(board.fen())
            if random.random() > threshold:
                sampledFenSet.append(board.fen())
            board.pop()
    sampledFenSet.extend(randomSearchSample(fenSet, depth-1))
    return sampledFenSet
    

In [117]:
#this takes the raw data and preprocesses it into features
#open the raw data
path = '/home/rvansoelen/rbmcData/isc_games/'
files = ['games1.json', 'games2.json', 'games3.json', 'games4.json']
start = time.time()
fenSet = []
print('Starting...')
for file in files:
    filepath = path+file
    with open(filepath, 'r') as fid:
        numLines = num_lines = sum(1 for line in fid)
    with open(filepath, 'r') as fid:
        dataset = []
        for i, line in enumerate(fid):
            if i%100 ==0: 
                print'Game', i, ' out of ', numLines
                print(time.time()-start)
            game = json.loads(line)
            if game['status'] != 'complete':
                print('Skipping game ', game['id'], ', status is ', game['status'])
                continue
            for j, turn in enumerate(game['gameHistory']):
                if turn['request'].get('action') != None and turn['request']['action']['action'] == 'move':
                    continue
                elif turn['response']['gameInfo'].get('status') == 'over':
                    continue
                fen = turn['truth']['fen']+' '+str(turn['moveNumber'])
                fenSet.extend(randomSearchSample(fen))
                
                #print boardFeatures
                #break
                
            #break
    #break
random.shuffle(fenSet)
print('Done')
print(time.time()-start)

Starting...
Game 0  out of  2730
0.0834851264954
Game 100  out of  2730
10.0694360733
Game 200  out of  2730
19.7264192104
Game 300  out of  2730
32.4937992096
Game 400  out of  2730
49.7195081711
Game 500  out of  2730
66.9804911613
Game 600  out of  2730
86.1469671726
Game 700  out of  2730
99.1556110382
Game 800  out of  2730
117.402672052
Game 900  out of  2730
132.095604181
Game 1000  out of  2730
151.133941174
Game 1100  out of  2730
171.236813068
Game 1200  out of  2730
191.25633812
Game 1300  out of  2730
207.745145082
Game 1400  out of  2730
222.803314209
Game 1500  out of  2730
238.931527138
Game 1600  out of  2730
253.749359131
Game 1700  out of  2730
271.395536184
Game 1800  out of  2730
289.74549818
Game 1900  out of  2730
308.639278173
Game 2000  out of  2730
324.674986124
Game 2100  out of  2730
335.996391058
Game 2200  out of  2730
342.994542122
Game 2300  out of  2730
344.386539221
Game 2400  out of  2730
353.591920137
Game 2500  out of  2730
361.159543991
Game 2600  o

In [ ]:
print fenSet[0]

In [ ]:
print('Starting...')
start = time.time()
checkRestartEngine(force=True)
boardFeatures = []
for i, fen in enumerate(fenSet):
    if i%1000 ==0: print'Board', i, ' out of ', len(fenSet)
    boardFeatures.extend(fen2Features(fen))
print len(boardFeatures), ' board-move samples generated'
outputFile = 'features.pckl'
with open(outputFile, 'wb') as fid:
    pickle.dump(boardFeatures, fid)
print('Done')
print(time.time()-start)

Starting...
Board 0  out of  641221
Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
h8g7
{'pv': {1: [Move.from_uci('h8g7'), Move.from_uci('f7g8'), Move.from_uci('d5e7')]}, 'seldepth': 6, 'tbhits': 0, 'refutation': {}, 'depth': 4, 'score': {1: Score(cp=1240, mate=None)}, 'nps': 191500, 'currline': {}, 'time': 2, 'nodes': 383, 'multipv': 1}


Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
h8f6
{'pv': {1: [Move.from_uci('h8f6'), Move.from_uci('f7e6'), Move.from_uci('f6e7')]}, 'seldepth': 6, 'tbhits': 0, 'refutation': {}, 'depth': 4, 'score': {1: Score(cp=3600, mate=None)}, 'nps': 145333, 'currline': {}, 'time': 3, 'nodes': 436, 'multipv': 1}


Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . .

Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
d1d2
{'pv': {1: [Move.from_uci('d1d2')]}, 'seldepth': 4, 'tbhits': 0, 'refutation': {}, 'depth': 4, 'score': {1: Score(cp=886, mate=None)}, 'nps': 37000, 'currline': {}, 'time': 2, 'nodes': 74, 'multipv': 1}


Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
d1e1
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
d1c1
{'pv': {1: [Move.from_uci('d1c1')]}, 'seldepth': 4, 'tbhits': 0, 'refutation': {}, 'depth': 4, 'score': {1: Score(cp=785, mate=None)}, 'nps': 10666, 'currline': {}, 'time': 3, 'nodes': 32, 'multipv': 1}


Error processing board and move:

Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
e5c4
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
e5f3
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
e5d3
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
d5e7
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .

Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
h2h4
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
f2f4
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
c2c4
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .
. . . . . . . .
. . . . . . P .
P P P . . P B P
R . . Q n . K .
b2b4
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . b . . b . B
p p q p p k . .
. . . . . . . p
. . P N N . p .

Error processing board and move:
. k . . . . . r
p . B . . b . p
. . . . . p P .
. p . . . . . .
. . . r . . . .
. . P . . . . .
P P . . . . P P
R B . . . R K .
g6h7
{'pv': {1: [Move.from_uci('g6h7'), Move.from_uci('b8c7'), Move.from_uci('f1f6')]}, 'seldepth': 5, 'tbhits': 0, 'refutation': {}, 'depth': 5, 'score': {1: Score(cp=886, mate=None)}, 'nps': 66000, 'currline': {}, 'time': 3, 'nodes': 198, 'multipv': 1}


Error processing board and move:
. k . . . . . r
p . B . . b . p
. . . . . p P .
. p . . . . . .
. . . r . . . .
. . P . . . . .
P P . . . . P P
R B . . . R K .
g6f7
{'pv': {1: [Move.from_uci('g6f7'), Move.from_uci('b8c7'), Move.from_uci('c3d4'), Move.from_uci('b5b4'), Move.from_uci('f1f6')]}, 'seldepth': 5, 'tbhits': 0, 'refutation': {}, 'depth': 5, 'score': {1: Score(cp=1187, mate=None)}, 'nps': 36000, 'currline': {}, 'time': 3, 'nodes': 108, 'multipv': 1}


Error processing board and move:
. k . . . . . r
p . B . . b . p
. . . . . p P .
. p . . . . . .
. . . r . . . .
. . 

...

Error processing board and move:
k . . . . . Q .
. . p . . R . P
. . . . . . . .
. . . . . . . .
P . . . . . . .
. . . . K . . .
. . . . . . . .
R r . . . . . .
f7c7
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
k . . . . . Q .
. . p . . R . P
. . . . . . . .
. . . . . . . .
P . . . . . . .
. . . . K . . .
. . . . . . . .
R r . . . . . .
f7f6
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
k . . . . . Q .
. . p . . R . P
. . . . . . . .
. . . . . . . .
P . . . . . . .
. . . . K . . .
. . . . . . . .
R r . . . . . .
f7f5
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
k . . . . . Q .
. . p . . R . P
. . . . . . . .
. . . . . . . .
P . . . . . . .
. . . . K . . .
. . . . . . . .
R r . . . . . .
f7f4
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
k . . . . . Q .
. . p . . R . P
. . . . . . . .
. . . . . . . .

Error processing board and move:
r . . . r . k .
p p . . . p p p
. . . b . . . .
. . n P . . . .
. . . . q P b .
. . N B . . P .
P P . B . . . P
R . . Q R . . K
g8f8
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . . . r . k .
p p . . . p p p
. . . b . . . .
. . n P . . . .
. . . . q P b .
. . N B . . P .
P P . B . . . P
R . . Q R . . K
e8f8
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . . . r . k .
p p . . . p p p
. . . b . . . .
. . n P . . . .
. . . . q P b .
. . N B . . P .
P P . B . . . P
R . . Q R . . K
e8d8
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . . . r . k .
p p . . . p p p
. . . b . . . .
. . n P . . . .
. . . . q P b .
. . N B . . P .
P P . B . . . P
R . . Q R . . K
e8c8
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . . . r . k .
p p . . . p p p
. . . b . . . .
. . n P . . . .

Error processing board and move:
r . . . r . k .
p p . . . p p p
. . . b . . . .
. . n P . . . .
. . . . q P b .
. . N B . . P .
P P . B . . . P
R . . Q R . . K
e4d5
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . . . r . k .
p p . . . p p p
. . . b . . . .
. . n P . . . .
. . . . q P b .
. . N B . . P .
P P . B . . . P
R . . Q R . . K
e4f4
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . . . r . k .
p p . . . p p p
. . . b . . . .
. . n P . . . .
. . . . q P b .
. . N B . . P .
P P . B . . . P
R . . Q R . . K
e4d4
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . . . r . k .
p p . . . p p p
. . . b . . . .
. . n P . . . .
. . . . q P b .
. . N B . . P .
P P . B . . . P
R . . Q R . . K
e4c4
{'refutation': {}, 'score': {}, 'pv': {}, 'currline': {}}


Error processing board and move:
r . . . r . k .
p p . . . p p p
. . . b . . . .
. . n P . . . .

Error processing board and move:
r . b . k . . r
p p p . . p . p
. . . . . q . p
. . . . . . . .
. . P . P . . .
. . Q . . . . .
P p . b B P P P
. . . R K . . R
c8g4
{'pv': {1: [Move.from_uci('c8g4')]}, 'seldepth': 7, 'tbhits': 0, 'refutation': {}, 'depth': 5, 'score': {1: Score(cp=-1175, mate=None)}, 'nps': 170000, 'currline': {}, 'time': 2, 'nodes': 340, 'multipv': 1}


Error processing board and move:
r . b . k . . r
p p p . . p . p
. . . . . q . p
. . . . . . . .
. . P . P . . .
. . Q . . . . .
P p . b B P P P
. . . R K . . R
c8h3
{'pv': {1: [Move.from_uci('c8h3')]}, 'seldepth': 7, 'tbhits': 0, 'refutation': {}, 'depth': 5, 'score': {1: Score(cp=-1234, mate=None)}, 'nps': 82666, 'currline': {}, 'time': 3, 'nodes': 248, 'multipv': 1}


Error processing board and move:
r . b . k . . r
p p p . . p . p
. . . . . q . p
. . . . . . . .
. . P . P . . .
. . Q . . . . .
P p . b B P P P
. . . R K . . R
a8b8
{'pv': {1: [Move.from_uci('a8b8')]}, 'seldepth': 7, 'tbhits': 0, 'refutation': {}, 'd

Error processing board and move:
r . b . k . . r
p p p . . p . p
. . . . . q . p
. . . . . . . .
. . P . P . . .
. . Q . . . . .
P p . b B P P P
. . . R K . . R
a7a6
{'pv': {1: [Move.from_uci('a7a6')]}, 'seldepth': 7, 'tbhits': 0, 'refutation': {}, 'depth': 5, 'score': {1: Score(cp=-1237, mate=None)}, 'nps': 98500, 'currline': {}, 'time': 2, 'nodes': 197, 'multipv': 1}


Error processing board and move:
r . b . k . . r
p p p . . p . p
. . . . . q . p
. . . . . . . .
. . P . P . . .
. . Q . . . . .
P p . b B P P P
. . . R K . . R
h6h5
{'pv': {1: [Move.from_uci('h6h5')]}, 'seldepth': 7, 'tbhits': 0, 'refutation': {}, 'depth': 5, 'score': {1: Score(cp=-1225, mate=None)}, 'nps': 116000, 'currline': {}, 'time': 2, 'nodes': 232, 'multipv': 1}


Error processing board and move:
r . b . k . . r
p p p . . p . p
. . . . . q . p
. . . . . . . .
. . P . P . . .
. . Q . . . . .
P p . b B P P P
. . . R K . . R
b2b1q
{'pv': {1: [Move.from_uci('b2b1q')]}, 'seldepth': 7, 'tbhits': 0, 'refutation': {}, 

In [96]:
boardFeatures[0].keys()

['pieceFeatures', 'labels', 'moveRankings', 'squareFeatures', 'globalFeatures']

In [16]:
#chess.Board(game['gameHistory'][12]['truth']['fen']+" 1")
#turn['response']
#game['gameHistory'][1]['response']['gameInfo']
#fen = turn['truth']['fen'] + " 1"
#chess.Board(fen)
#fen2Features(fen)

with open(filepath, 'r') as fid:
    lines = [line for line in fid]
len(lines)*len(fenSet)*3.0/1e6

1.64466

In [17]:
#get the boards and moves from each board

#augement data: (does this bias the representation of states??)
	#perform a time limited search on board states from raw data
	#randomly sample from this search to get dataset
	#label board state with best move, either from stockfish, raw data, or other person's bot
#fen
#db.set_trace()

In [18]:
#partition data into test, validation, and train

#num_lines = sum(1 for line in open(filepath))
#print num_lines
#randomly sort and save samples